In [81]:
import pandas as pd
import numpy as np
import time 
import re
from datetime import datetime

## Data Cleaning

In [57]:
rawData = pd.read_csv('data/SqlMetric_prepared.csv')
rawData.head()

Event Name  Time MSec          Process Name  \
0  UIServerEventSource/LoadDataStart/Start   2518.457  Process(2920) (2920)   
1    UIServerEventSource/LoadDataStop/Stop   2621.028  Process(2920) (2920)   
2  UIServerEventSource/LoadDataStart/Start   2621.106  Process(2920) (2920)   
3    UIServerEventSource/LoadDataStop/Stop   2700.351  Process(2920) (2920)   
4  UIServerEventSource/LoadDataStart/Start   2700.375  Process(2920) (2920)   

                                            criteria DURATION_MSEC  \
0  Key_backup_policy_tag_73391121-b001-4a9a-b2b2-...           NaN   
1  Key_backup_policy_tag_73391121-b001-4a9a-b2b2-...       102.572   
2  Key_@row_session_id_00000000-0000-0000-0000-00...           NaN   
3  Key_@row_session_id_00000000-0000-0000-0000-00...        79.245   
4                                                Key           NaN   

                                         metrics        timestamp usn  \
0  Table_1:47 Table_2:476 Table_3:199 Table_4:56  11/15/2019 9:51   0   
1  Table_1:47 Table_2:476 Table_3:199 Table_4:56  11/15/2019 9:51   0   
2  Table_1:47 Table_2:476 Table_3:199 Table_4:56  11/15/2019 9:51   0   
3  Table_1:47 Table_2:476 Table_3:199 Table_4:56  11/15/2019 9:51   0   
4  Table_1:47 Table_2:476 Table_3:199 Table_4:56  11/15/2019 9:51   0   

      viewName  ActivityID  
0  Procedure_0         NaN  
1  Procedure_0         NaN  
2  Procedure_1         NaN  
3  Procedure_1         NaN  
4  Procedure_2         NaN

In [58]:
rawData.drop(['ActivityID', 'Event Name', 'criteria', 'Process Name'], axis=1, inplace=True)

In [59]:
rawData.isnull().sum()

Time MSec             0
DURATION_MSEC    173975
metrics               0
timestamp             0
usn                   0
viewName              0
dtype: int64

In [60]:
rawData.dropna(inplace=True)
print(rawData.isnull().sum())
print('Dataset shape: {}'.format(rawData.shape))

Time MSec        0
DURATION_MSEC    0
metrics          0
timestamp        0
usn              0
viewName         0
dtype: int64
Dataset shape: (173974, 6)


In [61]:
rawData.head()

Time MSec DURATION_MSEC                                        metrics  \
1   2621.028       102.572  Table_1:47 Table_2:476 Table_3:199 Table_4:56   
3   2700.351        79.245  Table_1:47 Table_2:476 Table_3:199 Table_4:56   
5   2701.448         1.073  Table_1:47 Table_2:476 Table_3:199 Table_4:56   
7   6288.764      3,587.28  Table_1:47 Table_2:476 Table_3:199 Table_4:56   
9   6386.315        97.403  Table_1:47 Table_2:476 Table_3:199 Table_4:56   

         timestamp     usn     viewName  
1  11/15/2019 9:51       0  Procedure_0  
3  11/15/2019 9:51       0  Procedure_1  
5  11/15/2019 9:51       0  Procedure_2  
7  11/15/2019 9:51       0  Procedure_3  
9  11/15/2019 9:51  76,986  Procedure_4

In [62]:
rawData['db_state'] = rawData['metrics'].apply(lambda x: x.split(' '))
rawData.drop(['metrics'], axis=1, inplace=True)
print('Dataset shape: {}'.format(rawData.shape))
row = rawData.iloc[0,5]
print('Metrics: {}'.format(row))

dic = {}

for st in row:
    splitted = st.split(':')
    key = splitted[0] 
    dic[key] = [] 
    
print('Parsing sql metrics')
for index, row in rawData.iterrows():
    metrics_row = row['db_state']
    for i in range(0,4):
        st = metrics_row[i]
        splitted = st.split(':')
        key = 'Table_{}'.format(i+1)
        val = np.NaN   
        if len(splitted)>1:
            val = int(splitted[1])
        
        dic[key].append(val)
        

print('Adding new metrics collumns')     
for key in dic.keys():
    rawData[key] = dic[key]

print('Drop db_state column')
rawData.drop(['db_state'], axis=1, inplace=True)
    
print('Parsing sql metrics finnised')
print('Dataset shape: {}'.format(rawData.shape))

Dataset shape: (173974, 6)
Metrics: ['Table_1:47', 'Table_2:476', 'Table_3:199', 'Table_4:56']
Parsing sql metrics
Adding new metrics collumns
Drop db_state column
Parsing sql metrics finnised
Dataset shape: (173974, 9)


In [63]:
print(rawData.isnull().sum())

Time MSec           0
DURATION_MSEC       0
timestamp           0
usn                 0
viewName            0
Table_1          4844
Table_2          4844
Table_3          4844
Table_4          4844
dtype: int64


In [64]:
rawData.dropna(inplace=True)
print('Dataset shape: {}'.format(rawData.shape))

Dataset shape: (169130, 9)


In [111]:
def str_to_dt_safe(dt_string):
    # 11/15/2019 19:51:00.345
    m = re.match(r"\d{2}/\d{2}/\d{4} \d{2}:\d{2}:\d{2}\.\d+Z", dt_string)
    if m:
        return datetime.strptime(dt_string, "%m/%d/%Y %H:%M:%S.%f")
    # 11/15/2019 09:51:00.345
    m = re.match(r"\d{2}/\d{2}/\d{4} \d{1}:\d{2}:\d{2}\.\d+Z", dt_string)
    if m:
        return datetime.strptime(dt_string, "%m/%d/%Y %H:%M:%S.%f")
    # 11/15/2019 19:51:00
    m = re.match(r"\d{2}/\d{2}/\d{4} \d{2}:\d{2}:\d{2}", dt_string)
    if match:
        return datetime.strptime(dt_string, "%m/%d/%Y %H:%M:%S")
    # 11/15/2019 9:51:00
    m = re.match(r"\d{2}/\d{2}/\d{4} \d{1}:\d{2}:\d{2}", dt_string)
    if match:
        return datetime.strptime(dt_string, "%m/%d/%Y %H:%M:%S")
    # 11/15/2019 19:51
    m = re.match(r"\d{2}/\d{2}/\d{4} \d{2}:\d{2}",dt_string)
    if match:
        return datetime.strptime(dt_string, "%m/%d/%Y %H:%M")
     # 11/15/2019 09:51
    m = re.match(r"\d{2}/\d{2}/\d{4} \d{1}:\d{2}", dt_string)
    if match:
        return datetime.strptime(dt_string, "%m/%d/%Y %H:%M")
    # unknown timestamp format
    print("Unknown timestamp format {}".format(dt_string))
    return np.NaN

In [110]:
rawData = rawData.applymap(lambda x: x.replace(',','') if type(x) is str or type(x) is object else x)
rawData['is_cold_start'] = rawData['usn'].apply(lambda x: True if int(x) == 0 else False)
rawData.drop(['usn'], axis=1, inplace=True)
rawData.rename(columns={'Time MSec': 'timestamp', 'DURATION_MSEC': 'duration', 'timestamp':'time'}, inplace=True)
rawData['duration'] = rawData['duration'].apply(lambda x: float(x))

rawData['time'] = rawData['time'].apply(lambda x: str_to_dt_safe(x))
    
rawData.head()

Unknown timestamp format 17:51:23.594656 (15316.271 MSec)
Unknown timestamp format 17:51:23.612594 (15334.209 MSec)
Unknown timestamp format 17:51:28.125961 (19847.576 MSec)
Unknown timestamp format 17:51:28.891598 (20613.212 MSec)
Unknown timestamp format 17:51:29.360356 (21081.971 MSec)
Unknown timestamp format 17:51:30.316792 (22038.407 MSec)
Unknown timestamp format 17:51:31.407259 (23128.874 MSec)
Unknown timestamp format 17:51:31.800383 (23521.997 MSec)
Unknown timestamp format 17:51:37.344838 (29066.453 MSec)
Unknown timestamp format 17:51:37.447212 (29168.827 MSec)
Unknown timestamp format 17:51:37.447212 (29168.827 MSec)
Unknown timestamp format 17:51:37.579215 (29300.830 MSec)
Unknown timestamp format 17:51:40.688636 (32410.250 MSec)
Unknown timestamp format 17:51:40.782382 (32503.997 MSec)
Unknown timestamp format 17:51:40.782382 (32503.997 MSec)
Unknown timestamp format 17:51:41.407404 (33129.019 MSec)
Unknown timestamp format 17:51:41.469895 (33191.509 MSec)
Unknown timest

KeyboardInterrupt: 

## Studing data

In [68]:
data = pd.DataFrame(rawData)

In [69]:
data.dtypes

timestamp        float64
duration         float64
time              object
viewName          object
Table_1          float64
Table_2          float64
Table_3          float64
Table_4          float64
is_cold_start       bool
dtype: object